In [24]:
"""
Merges FIFA(ITMO) and KudaGo datasets
Input:
FIFA(ITMO) and KudaGo datasets as .json files,
list of place correspondence based on distance.
Output: Dataset with places from both FIFA and KudaGo.
"""


import json
from json import JSONDecodeError
from geopy import distance


location = "spb"    # choose location here (spb, msk)

# Directory and in/out files:
direct = "D:/Work/Data_files/working_dir/"
KudaGo_file = "new_format_"
FIFA_file = "ds_FIFA_"
twin_places = "twins_"
merged_ds = "merged_ds_"

# Treshold distance for similarity check, km:
treshold_dist = 0.05

with open(direct + KudaGo_file + location + ".json",
           'r', encoding = "utf-8") as KGo_f, \
     open(direct + FIFA_file + location + ".json",
           'r', encoding = "utf-8") as FIFA_f, \
     open(direct + twin_places + location + ".json",
           'r', encoding = "utf-8") as twin_list, \
     open(direct + merged_ds + location + ".json",
           'w', encoding = "utf-8") as ouf:
    try:
        FIFA_ds = json.load(FIFA_f)
        KudaGo_ds = json.load(KGo_f)
        
        # Correspondence of two previous datasets,
        # based on distance similarity.
        # output of 'distances_similarity.ipynb'
        twins_as_list = json.load(twin_list)
        
        # Make dictionary without empty fields from twins list
        twins = {}
        for twin in twins_as_list:
            if twin:
                twins.update(twin)

        merged = []
        count_match = 0
        for FIFA_place in FIFA_ds:
            # If place from FIFA ds has similarities
            # with place/places from KudaGo ds            
            if FIFA_place['title'] in twins:
                
                FIFA_coord = (FIFA_place["lat"],
                              FIFA_place["lng"])
                
                min_dist = treshold_dist
                match = {}
                
                for KudaGo_title in twins[FIFA_place['title']]:                    
                    for KudaGo_place in KudaGo_ds:
                        if KudaGo_place['title'] == KudaGo_title:
                            
                            KudaGo_coord = (KudaGo_place["lat"],
                                            KudaGo_place["lng"])
                             
                            dist = distance.distance(
                                FIFA_coord, KudaGo_coord).km
                            
                            if dist < min_dist:
                                min_dist = dist
                                # the nearest place in KudaGo ds
                                match = KudaGo_place
                                print("\nNearest to: ", FIFA_place['title'])
                                print(match['title'])
                                
                # 'if match' checks the possibility, that the place
                # has been alredy taken from KudaGo ds in previous 
                # cycles, but still in twins list.
                if match:
                    
                    # to avoid double-counting the place 
                    KudaGo_ds.remove(match)
                    count_match += 1
                    
                    # Add KudaGo metrics to FIFA place:
                    FIFA_place["id_KudaGo"] = match["id_KudaGo"]
                    FIFA_place["favorites_count_KudaGo"] =\
                        match["favorites_count_KudaGo"]
                    FIFA_place["comments_count_KudaGo"] =\
                        match["comments_count_KudaGo"]
                    FIFA_place["events_count_KudaGo"] =\
                        match["events_count_KudaGo"]
                    if match["additional_categories"]:
                        if FIFA_place["additional_categories"]:
                            FIFA_place["additional_categories"] +=\
                                match["additional_categories"]
                        else:
                            FIFA_place["additional_categories"] =\
                                match["additional_categories"]
            # If no silmilarities than just add fields empty
            else:
                FIFA_place["id_KudaGo"] = None
                FIFA_place["favorites_count_KudaGo"] = None
                FIFA_place["comments_count_KudaGo"] = None
                FIFA_place["events_count_KudaGo"] = None
                
            print("\n\nFIFA place: ", FIFA_place)
            merged.append(FIFA_place)
        
        # only places wiithout similarities
        # still remains in 'KudaGo_ds'
        for KudaGo_place in KudaGo_ds:
            merged.append(KudaGo_place)
        json.dump(merged, ouf)
    except JSONDecodeError:
        print("JSONDecodeError")
   

with open(direct + KudaGo_file + location + ".json",
           'r', encoding = "utf-8") as KGo_f, \
     open(direct + FIFA_file + location + ".json",
           'r', encoding = "utf-8") as FIFA_f, \
     open(direct + twin_places + location + ".json",
           'r', encoding = "utf-8") as twin_list, \
     open(direct + merged_ds + location + ".json",
           'r', encoding = "utf-8") as merged:  
    twins_set = json.load(twin_list)
    FIFA_ds = json.load(FIFA_f)
    KudaGo_ds = json.load(KGo_f)
    merged_ds= json.load(merged)
    twins_num = 0
    for twins in twins_set:
        if twins:
            twins_num += 1
    print("Number of twins for ", location)
    print(twins_num)
    print("Number of places in KudaGo ds ", len(KudaGo_ds))
    print("Number of places in FIFA ds ", len(FIFA_ds))
    print("Number of places in merged ds ", len(merged_ds))
    print("Matches count: ", count_match)



FIFA place:  {'additional_categories': ['Religious Center', 'Baptist Church'], 'address': 'Griboyedov Canal Emb., 2A, St. Petersburg 191011, Russia', 'categories': ['Sights & Landmarks'], 'city_brand': ['Venice of the North'], 'duration': 15, 'facebook_checkins': 73614.0, 'facebook_rating': 376.0, 'foursquare_checkinsCount': None, 'foursquare_rating': None, 'foursquare_ratingVotes': None, 'foursquare_userCount': None, 'image': 'https://commons.wikimedia.org/wiki/File:Собор_Воскресения_Христова_1.jpg', 'instagram_title': None, 'instagram_visitorsNumber': 245694.0, 'lat': 59.940094, 'lng': 30.328583, 'open_hours': {'0': [1030, 1800], '1': [1030, 1800], '2': [1030, 1800], '3': [1030, 1800], '4': [1030, 1800], '5': [1030, 1800], '6': [1030, 1800]}, 'title': 'Church of the Savior on Spilled Blood', 'tripAdvisor_rating': 5.0, 'tripAdvisor_reviewsNumber': 17350.0, 'wikipedia_page': 1, 'wikipedia_title': 'Спас на Крови', 'x': 3376162.4160415325, 'y': 8386412.538746054, 'id_KudaGo': None, 'fa

FIFA place:  {'additional_categories': None, 'address': 'Mirgorodskaya St., 1B, St. Petersburg 191024, Russia', 'categories': ['Museums & Libraries'], 'city_brand': [], 'duration': 120, 'facebook_checkins': None, 'facebook_rating': None, 'foursquare_checkinsCount': None, 'foursquare_rating': None, 'foursquare_ratingVotes': None, 'foursquare_userCount': None, 'image': None, 'instagram_title': None, 'instagram_visitorsNumber': None, 'lat': 59.926296, 'lng': 30.369495, 'open_hours': None, 'title': 'The ADAMA Artistic Studio of Tin Miniatures', 'tripAdvisor_rating': 5.0, 'tripAdvisor_reviewsNumber': 2.0, 'wikipedia_page': 0, 'wikipedia_title': None, 'x': 3380716.7190488684, 'y': 8383346.755334936, 'id_KudaGo': None, 'favorites_count_KudaGo': None, 'comments_count_KudaGo': None, 'events_count_KudaGo': None}


FIFA place:  {'additional_categories': None, 'address': 'Zheleznodorozhnaya St., 2, St. Petersburg 198205, Russia', 'categories': ['Sights & Landmarks'], 'city_brand': [], 'duration': 


Nearest to:  Coverdale
ресторан DIZZY


FIFA place:  {'additional_categories': ['Restaurant', 'Pub', 'restaurants', 'bar'], 'address': 'Emb. Kanala Griboyedova, 36, St. Petersburg 191023, Russia ', 'categories': ['Restaurant'], 'city_brand': [], 'duration': 60, 'facebook_checkins': None, 'facebook_rating': None, 'foursquare_checkinsCount': None, 'foursquare_rating': None, 'foursquare_ratingVotes': None, 'foursquare_userCount': None, 'image': None, 'instagram_title': None, 'instagram_visitorsNumber': None, 'lat': 59.93104, 'lng': 30.32151, 'open_hours': None, 'title': 'Coverdale', 'tripAdvisor_rating': 0.0, 'tripAdvisor_reviewsNumber': 0.0, 'wikipedia_page': 0, 'wikipedia_title': None, 'x': 3375375.053283154, 'y': 8384400.682830051, 'id_KudaGo': 31724, 'favorites_count_KudaGo': 0, 'comments_count_KudaGo': 0, 'events_count_KudaGo': 1}


FIFA place:  {'additional_categories': ['Restaurant', 'Cafe'], 'address': 'Gakkelevskaya, 21 Bldg. A, St. Petersburg 197227, Russia ', 'categories': ['R



FIFA place:  {'additional_categories': ['Restaurant', 'European', 'Spanish'], 'address': 'Dumskaya St., 1, St. Petersburg 191011, Russia ', 'categories': ['Restaurant'], 'city_brand': [], 'duration': 60, 'facebook_checkins': None, 'facebook_rating': None, 'foursquare_checkinsCount': None, 'foursquare_rating': None, 'foursquare_ratingVotes': None, 'foursquare_userCount': None, 'image': None, 'instagram_title': None, 'instagram_visitorsNumber': None, 'lat': 59.93401, 'lng': 30.328852, 'open_hours': {'6': [1200, 3000], '0': [1200, 3000], '1': [1200, 3000], '2': [1200, 3000], '3': [1200, 3000], '4': [1200, 3000], '5': [1200, 3000]}, 'title': 'Barslona', 'tripAdvisor_rating': 0.0, 'tripAdvisor_reviewsNumber': 0.0, 'wikipedia_page': 0, 'wikipedia_title': None, 'x': 3376192.360984555, 'y': 8385060.575036431}

Nearest to:  Bar Nebar 2.0
бар Nebar 2.0

Nearest to:  Bar Nebar 2.0
«Руки Вверх бар»


FIFA place:  {'additional_categories': ['Restaurant', 'Russian', 'Dance & Night Club', 'Pub', 'C


Nearest to:  Lucky Shot
ресторан «Оливье»


FIFA place:  {'additional_categories': ['Restaurant', 'European', 'Grill', 'Russian', 'restaurants'], 'address': 'Gorokhovaya St., 3, St. Petersburg 190000, Russia ', 'categories': ['Restaurant'], 'city_brand': [], 'duration': 60, 'facebook_checkins': None, 'facebook_rating': None, 'foursquare_checkinsCount': None, 'foursquare_rating': None, 'foursquare_ratingVotes': None, 'foursquare_userCount': None, 'image': None, 'instagram_title': None, 'instagram_visitorsNumber': None, 'lat': 59.935814, 'lng': 30.310314, 'open_hours': {'6': [1200, 2400], '0': [1200, 2400], '1': [1200, 2400], '2': [1200, 2400], '3': [1200, 2400], '4': [1200, 2400], '5': [1200, 2400]}, 'title': 'Lucky Shot', 'tripAdvisor_rating': 0.0, 'tripAdvisor_reviewsNumber': 0.0, 'wikipedia_page': 0, 'wikipedia_title': None, 'x': 3374128.7202642327, 'y': 8385461.427297407, 'id_KudaGo': 16012, 'favorites_count_KudaGo': 3, 'comments_count_KudaGo': 0, 'events_count_KudaGo': 0}


FIFA p

...



FIFA place:  {'additional_categories': ['Pier'], 'address': 'Россия', 'categories': ['Sights & Landmarks'], 'city_brand': ['Venice of the North'], 'duration': 15, 'facebook_checkins': None, 'facebook_rating': None, 'foursquare_checkinsCount': 4.0, 'foursquare_rating': None, 'foursquare_ratingVotes': None, 'foursquare_userCount': 4.0, 'image': None, 'instagram_title': None, 'instagram_visitorsNumber': None, 'lat': 60.1351010198, 'lng': 30.612985479, 'open_hours': None, 'title': 'Мост через Морье', 'tripAdvisor_rating': None, 'tripAdvisor_reviewsNumber': None, 'wikipedia_page': 0, 'wikipedia_title': None, 'x': 3407821.955185459, 'y': 8429878.261404008, 'id_KudaGo': None, 'favorites_count_KudaGo': None, 'comments_count_KudaGo': None, 'events_count_KudaGo': None}


FIFA place:  {'additional_categories': ['Exhibit'], 'address': 'Россия', 'categories': ['Museums & Libraries'], 'city_brand': [], 'duration': 120, 'facebook_checkins': None, 'facebook_rating': None, 'foursquare_checkinsCount':

FIFA place:  {'additional_categories': ['Bakery'], 'address': 'Ул. Советская 33 Б Кронштадт Россия', 'categories': ['Restaurant'], 'city_brand': [], 'duration': 60, 'facebook_checkins': None, 'facebook_rating': None, 'foursquare_checkinsCount': 634.0, 'foursquare_rating': 7.6, 'foursquare_ratingVotes': 142.0, 'foursquare_userCount': 946.0, 'image': None, 'instagram_title': None, 'instagram_visitorsNumber': None, 'lat': 59.9936886197, 'lng': 29.778114745, 'open_hours': {'0': [800, 2000], '1': [800, 2000], '2': [800, 2000], '3': [800, 2000], '4': [800, 2000], '5': [900, 2000], '6': [900, 2000]}, 'title': 'Кафе-пекарня Briosh', 'tripAdvisor_rating': None, 'tripAdvisor_reviewsNumber': None, 'wikipedia_page': 0, 'wikipedia_title': None, 'x': 3314884.5701932027, 'y': 8398332.864557771, 'id_KudaGo': None, 'favorites_count_KudaGo': None, 'comments_count_KudaGo': None, 'events_count_KudaGo': None}


FIFA place:  {'additional_categories': ['Statue & Fountain', 'Outdoor Sculpture'], 'address': 'у

FIFA place:  {'additional_categories': ['Doner Restaurant'], 'address': 'Соборная ул. (ул. Карла Маркса) Гатчина Россия', 'categories': ['Restaurant'], 'city_brand': [], 'duration': 60, 'facebook_checkins': None, 'facebook_rating': None, 'foursquare_checkinsCount': 793.0, 'foursquare_rating': 7.4, 'foursquare_ratingVotes': 118.0, 'foursquare_userCount': 1725.0, 'image': None, 'instagram_title': None, 'instagram_visitorsNumber': None, 'lat': 59.5657047344, 'lng': 30.1272490459, 'open_hours': None, 'title': 'Шаверма', 'tripAdvisor_rating': None, 'tripAdvisor_reviewsNumber': None, 'wikipedia_page': 0, 'wikipedia_title': None, 'x': 3353750.0227895617, 'y': 8303675.137954475, 'id_KudaGo': None, 'favorites_count_KudaGo': None, 'comments_count_KudaGo': None, 'events_count_KudaGo': None}


FIFA place:  {'additional_categories': ['Bar'], 'address': 'Россия', 'categories': ['Restaurant'], 'city_brand': [], 'duration': 60, 'facebook_checkins': None, 'facebook_rating': None, 'foursquare_checkinsCo

FIFA place:  {'additional_categories': ['church', 'place_of_worship', 'point_of_interest', 'establishment'], 'address': "Rostovskaya Ulitsa, 10, Shushary, Leningradskaya oblast', Russia, 196634", 'categories': ['Sights & Landmarks'], 'city_brand': ['Venice of the North'], 'duration': 15, 'facebook_checkins': None, 'facebook_rating': None, 'foursquare_checkinsCount': None, 'foursquare_rating': None, 'foursquare_ratingVotes': None, 'foursquare_userCount': None, 'image': 'https://commons.wikimedia.org/wiki/File:Slavyanka._Theotokos_Skoroposlushnitsa_church.jpg', 'instagram_title': None, 'instagram_visitorsNumber': None, 'lat': 59.7372972222, 'lng': 30.464925, 'open_hours': None, 'title': 'Церковь иконы Божией Матери «Скоропослушница» (Славянка)', 'tripAdvisor_rating': None, 'tripAdvisor_reviewsNumber': None, 'wikipedia_page': 1, 'wikipedia_title': 'Церковь иконы Божией Матери «Скоропослушница» (Славянка)', 'x': 3391339.9380552694, 'y': 8341480.826528187, 'id_KudaGo': None, 'favorites_coun

Number of twins for  spb
1640
Number of places in KudaGo ds  3736
Number of places in FIFA ds  10252
Number of places in merged ds  13184
Matches count:  804
